# Data Analysis Script

This notebook performs comprehensive data analysis including preprocessing, statistical analysis, and machine learning techniques.

**Created on:** Sat Oct 28 16:00:55 2023  
**Author:** mm

## 1. Import Libraries

In [ ]:
import pandas as pd
import numpy as np
from sklearn.preprocessing import StandardScaler, MinMaxScaler
import matplotlib.pyplot as plt
import seaborn as sns
from statsmodels.formula.api import ols
from statsmodels.stats.multicomp import MultiComparison
import statsmodels.api as sm
from scipy.stats import pearsonr
from sklearn.decomposition import PCA
import scipy.cluster.hierarchy as sch
from sklearn.cross_decomposition import PLSRegression
from sklearn.model_selection import cross_val_predict
from sklearn.metrics import accuracy_score, confusion_matrix, classification_report
from sklearn.preprocessing import LabelEncoder
from statsmodels.stats.multicomp import pairwise_tukeyhsd
from sklearn.experimental import enable_iterative_imputer  # noqa
from sklearn.impute import IterativeImputer
from mpl_toolkits.mplot3d import Axes3D
from itertools import combinations

## 2. Import Data

In [ ]:
# Import data
df = pd.read_csv("data_rice.csv", sep=",")
print(df.columns.values.tolist())
print(df.dtypes)

## 3. Data Preprocessing

In [ ]:
# Create a copy of the dataframe
XY = df.copy()

# Step 1: Check column types and separate qualitative and quantitative data
qualitative_cols = [col for col in XY.columns if XY[col].dtype == 'object']
quantitative_cols = [col for col in XY.columns if col not in qualitative_cols]

# Step 2: Separate columns containing a mix of text and numbers
mixed_cols = [col for col in qualitative_cols if XY[col].apply(lambda x: isinstance(x, str) and any(c.isdigit() for c in x) and any(c.isalpha() for c in x)).any()]
mixed_df = XY[mixed_cols].copy()

# Step 3: Identify text columns without missing or mixing
text_no_mix_missing = [col for col in qualitative_cols if col not in mixed_cols and not XY[col].isnull().any()]

# Step 4: Identify text columns with missing data
text_missing = [col for col in qualitative_cols if XY[col].isnull().any()]

# Step 5: Identify qualitative columns without missing data
qualitative_no_missing = [col for col in qualitative_cols if col not in mixed_cols and col not in text_missing]

# Step 6: Identify qualitative columns with missing data
qualitative_missing = [col for col in qualitative_cols if col not in mixed_cols and col not in text_no_mix_missing]

# Step 7: Identify quantitative columns without missing data
quantitative_no_missing = [col for col in quantitative_cols if not XY[col].isnull().any()]

# Step 8: Identify quantitative columns with missing data
quantitative_missing = [col for col in quantitative_cols if XY[col].isnull().any()]

# Step 9: Separate mixed columns into those with missing and those without
mixed_no_missing = [col for col in mixed_cols if not XY[col].isnull().any()]
mixed_missing = [col for col in mixed_cols if XY[col].isnull().any()]

# Step 10: Order columns as specified
ordered_cols = text_no_mix_missing + qualitative_no_missing + quantitative_no_missing + mixed_no_missing + text_missing + qualitative_missing + quantitative_missing + mixed_missing

# Now, XY contains all columns ordered as specified
XY = XY[ordered_cols]

# Step 11: Drop columns with duplicate names, keeping only the first entry
XY = XY.loc[:, ~XY.columns.duplicated()]

# Keep only selected columns
keep_cols = mixed_no_missing + text_no_mix_missing + qualitative_no_missing + quantitative_no_missing 
XY = XY[keep_cols]

print("\nCleaned DataFrame XY:")
print(XY)

## 4. Handle Numeric Categorical Columns

In [ ]:
# This function identifies numeric columns in the DataFrame that can be considered categorical
def find_numeric_categorical_columns(df, max_categories=5):
    numeric_categorical_cols = []
    
    for column in df.select_dtypes(include=['int64', 'float64']).columns:
        unique_values = df[column].nunique()
        
        # Check if the column has a limited number of unique values
        if unique_values <= max_categories:
            numeric_categorical_cols.append(column)
    
    return numeric_categorical_cols

# This function converts specified columns in the DataFrame to categorical data type
def convert_to_categorical(df, columns):
    for column in columns:
        df[column] = df[column].astype('category')
    return df

# Example usage:
df_all = df.copy()
numeric_categorical_columns = find_numeric_categorical_columns(df, max_categories=5)
df = convert_to_categorical(df, numeric_categorical_columns)

print(df.dtypes)

## 5. Remove Sequential Numeric Columns

In [ ]:
# Function to remove columns that contain sequential numerical counting
def remove_sequential_numeric_columns(df):
    columns_to_drop = []
    
    for column in df.columns:
        # Check if the column is a numeric column
        if pd.api.types.is_numeric_dtype(df[column]):
            # Sort values and check if they are sequential starting from 1
            sorted_values = df[column].dropna().sort_values().unique()
            if (sorted_values == range(1, len(sorted_values) + 1)).all():
                columns_to_drop.append(column)
    
    # Drop identified columns
    df = df.drop(columns=columns_to_drop)
    return df

# Example usage:
df = remove_sequential_numeric_columns(df)

# Function to convert object columns in a DataFrame to categorical type
def convert_object_to_categorical(df):
    for column in df.select_dtypes(include='object').columns:
        df[column] = df[column].astype('category')
    return df

# Convert object columns to categorical
df = convert_object_to_categorical(df)
print(df.dtypes)

## 6. Separate and Normalize Quantitative Data

In [ ]:
# Selecting only non-numeric (qualitative) columns
qualitative_data = df.select_dtypes(exclude=['number'])
# Selecting only numeric (quantitative) columns
quantitative_data = df.select_dtypes(include=['number'])

# 1. Normalize the quantitative data using z-scores
scaler_z = StandardScaler()
quantitative_data_z = pd.DataFrame(scaler_z.fit_transform(quantitative_data), columns=quantitative_data.columns)

# 2. Normalize the quantitative data using Min-Max scaling
scaler_mm = MinMaxScaler()
quantitative_data_mm = pd.DataFrame(scaler_mm.fit_transform(quantitative_data), columns=quantitative_data.columns)

# Displaying the first few rows of the normalized data
quantitative_data_z.head(), quantitative_data_mm.head()

## 7. Quantitative Analysis

In [ ]:
quantitative_vars = df.select_dtypes(include=['int', 'float']).columns.tolist()

# Applying Min-Max Normalization to the quantitative variables
scaler = MinMaxScaler()
df_min_max = df.copy()
df_min_max[quantitative_vars] = scaler.fit_transform(df[quantitative_vars])

# Function to create boxplots for normalized and non-normalized data
def plot_boxplots(df_original, df_normalized, variables):
    fig, axs = plt.subplots(nrows=2, figsize=(15, 10))

    sns.boxplot(data=df_original[variables], ax=axs[0])
    axs[0].set_title('Boxplot (Original Data)', fontsize=16)
    axs[0].tick_params(axis='x', rotation=45)

    sns.boxplot(data=df_normalized[variables], ax=axs[1])
    axs[1].set_title('Boxplot (Normalized Data)', fontsize=16)
    axs[1].tick_params(axis='x', rotation=45)

    plt.tight_layout()
    plt.show()

# Creating boxplots for all variables together
plot_boxplots(df, df_min_max, quantitative_vars)

df_descr = df.describe()
df_descr.to_csv('03df_descr.csv', index=False)

## 8. Calculate Mean and RSD by Category

In [ ]:
# Automatically detect quantitative and categorical columns
categorical_columns = df.select_dtypes(include=['object', 'category']).columns
quantitative_columns = df.select_dtypes(include=[np.number]).columns

# Dictionary to store combined results for each categorical column
combined_results = {}

# Loop through each categorical column to calculate grouped means and RSDs
for cat_col in categorical_columns:
    # Select only the quantitative columns along with the current categorical column for grouping
    DT = df[[cat_col] + list(quantitative_columns)]
    
    # Calculate mean and RSD for each group based on the current categorical column
    DT_mean = DT.groupby(cat_col).mean().round(3)
    DT_rsd = (DT.groupby(cat_col).std() / DT.groupby(cat_col).mean() * 100).round(1)
    
    # Combine the means and RSDs by interleaving columns
    combined_df = pd.DataFrame()
    for col in DT_mean.columns:
        combined_df[col + '_mean'] = DT_mean[col]
        combined_df[col + '_sd'] = DT_rsd[col]
    
    # Save the individual results to CSV (optional)
    DT_mean.to_csv(f'{cat_col}_DT_mean.csv', index=True)
    DT_rsd.to_csv(f'{cat_col}_DT_rsd.csv', index=True)
    combined_df.to_csv(f'{cat_col}_combined_mean_sd.csv', index=True)
    
    # Store the combined result in the dictionary with the categorical column as key
    combined_results[cat_col] = combined_df

# If you want to combine all results into one large DataFrame with hierarchical columns
final_combined_df = pd.concat(combined_results, axis=1)
final_combined_df.to_csv('all_categoricals_combined_mean_sd.csv')

## 9. Outlier Detection

In [ ]:
# Define your detect_outliers function
def detect_outliers(series):
    # Example: Using the IQR method
    Q1 = series.quantile(0.25)
    Q3 = series.quantile(0.75)
    IQR = Q3 - Q1
    return (series < (Q1 - 1.5 * IQR)) | (series > (Q3 + 1.5 * IQR))

# Automatically detect quantitative and categorical columns
categorical_columns = df.select_dtypes(include=['object', 'category']).columns
quantitative_columns = df.select_dtypes(include=[np.number]).columns

# Dictionary to store outlier DataFrames for each categorical column
outliers_results = {}

# Loop through each categorical column
for cat_col in categorical_columns:
    # Select quantitative columns along with the current categorical column for grouping
    outliers_df = df[[cat_col] + list(quantitative_columns)].copy()

    # Detect outliers for each numeric column grouped by the categorical column
    for col in quantitative_columns:
        outliers_df[col] = df.groupby(cat_col)[col].transform(detect_outliers)

    # Filter rows with at least one outlier in any of the quantitative columns
    outliers_sel = outliers_df[quantitative_columns].any(axis=1)
    outliers_sel_df = df[outliers_sel]

    # Replace outliers with missing data (NA) in a copy of the DataFrame
    dfNA = df[[cat_col] + list(quantitative_columns)].copy()
    for col in quantitative_columns:
        # Apply outlier detection within each group and align the index properly
        outlier_mask = df.groupby(cat_col)[col].transform(lambda x: detect_outliers(x))
        dfNA[col] = df[col].where(~outlier_mask)

    # Count missing values per column and in total for each categorical grouping
    na_count = dfNA.isna().sum()
    total_na_count = dfNA.isna().sum().sum()

    # Save results to CSV files
    outliers_df.to_csv(f'outliers_df_{cat_col}.csv', index=False)
    dfNA.to_csv(f'dfNA_{cat_col}.csv', index=False)
    
    # Store results in a dictionary for easy access or further analysis if needed
    outliers_results[cat_col] = {
        'outliers_df': outliers_df,
        'outliers_sel_df': outliers_sel_df,
        'dfNA': dfNA,
        'na_count': na_count,
        'total_na_count': total_na_count
    }

# Print missing value counts for each categorical grouping
for cat_col, results in outliers_results.items():
    print(f"Missing value counts for {cat_col}:")
    print(results['na_count'])
    print(f"Total missing values: {results['total_na_count']}\n")

## 10. Missing Value Imputation

In [ ]:
# Convert each categorical column to numerical codes for imputation
dfNA = df.copy()
for cat_col in categorical_columns:
    dfNA[cat_col] = pd.Categorical(dfNA[cat_col]).codes

# Initialize MICE imputer
mice_imputer = IterativeImputer(random_state=123, max_iter=50, imputation_order='ascending')

# Perform MICE imputation
dfNA_imputed = mice_imputer.fit_transform(dfNA)

# Convert imputed data back to DataFrame
dfNA_imputed = pd.DataFrame(dfNA_imputed, columns=dfNA.columns)

# Convert numerical codes back to original categorical values
for cat_col in categorical_columns:
    original_categories = df[cat_col].astype('category').cat.categories
    dfNA_imputed[cat_col] = pd.Categorical.from_codes(dfNA_imputed[cat_col].astype(int), categories=original_categories)

# Select columns needed for further processing
Xlm = dfNA_imputed[quantitative_columns]

## 11. Qualitative Analysis

In [ ]:
# Detect categorical columns
categorical_columns = df.select_dtypes(include=['object', 'category']).columns

# Check if there are categorical columns
if len(categorical_columns) == 0:
    print("No categorical columns found in the DataFrame.")
elif len(categorical_columns) == 1:
    # Handle case with only one categorical column
    col = categorical_columns[0]
    print(f"Only one categorical column found: {col}")
    
    # Plot frequency distribution
    plt.figure(figsize=(8, 5))
    sns.countplot(x=col, data=df, palette='viridis')
    plt.title(f'Frequency Distribution of {col}')
    plt.tight_layout()
    plt.show()
else:
    # Handle case with multiple categorical columns
    print("Multiple categorical columns found. Generating contingency tables and plots.")
    
    # Create pairwise contingency tables
    for col1, col2 in combinations(categorical_columns, 2):
        # Generate contingency table for each pair of categorical columns
        contingency_table = pd.crosstab(df[col1], df[col2])
        
        # Print and save contingency table
        print(f"Contingency Table {col1} vs {col2}:")
        print(contingency_table)
        contingency_table.to_csv(f'contingency_table_{col1}_vs_{col2}.csv', index=True)

    # Plot frequency distributions for each categorical column
    fig, axes = plt.subplots(1, len(categorical_columns), figsize=(6 * len(categorical_columns), 5))
    
    for i, col in enumerate(categorical_columns):
        sns.countplot(ax=axes[i], x=col, data=df, palette='viridis')
        axes[i].set_title(f'Frequency Distribution of {col}')
    
    plt.tight_layout()
    plt.show()

## 12. ANOVA and Tukey's HSD Test

In [ ]:
# Function to perform ANOVA and Tukey's HSD test
def anova_tukey(data, quantitative_vars, qualitative_vars):
    results = []
    
    for q_var in quantitative_vars:
        for ql_var in qualitative_vars:
            # Building the ANOVA model
            model = ols(f'{q_var} ~ C({ql_var})', data=data).fit()
            
            # Performing ANOVA
            anova_table = sm.stats.anova_lm(model, typ=2)
            
            # Performing Tukey's HSD test
            mc = MultiComparison(data[q_var], data[ql_var])
            tukey_result = mc.tukeyhsd()
            
            # Appending results to the list
            results.append({
                'Quantitative Variable': q_var,
                'Qualitative Variable': ql_var,
                'ANOVA': anova_table,
                'Tukey': tukey_result
            })
            
    return results

# Performing ANOVA and Tukey's HSD test for quantitative variables vs qualitative variables
quantitative_vars = df.select_dtypes(include=['int', 'float']).columns.tolist()
qualitative_vars = df.select_dtypes(include=['object', 'category']).columns.tolist()

anova_results = anova_tukey(df, quantitative_vars, qualitative_vars)

# Save results to CSV
results_df = pd.DataFrame(anova_results)
results_df.to_csv('05anova_results.csv', index=False)

## 13. Bivariate Analysis

In [ ]:
# Correlation matrix
correlation_matrix = df[quantitative_vars].corr()

# Plotting the correlation matrix
plt.figure(figsize=(10, 8))
sns.heatmap(correlation_matrix, annot=True, fmt=".2f", cmap='coolwarm', vmin=-1, vmax=1)
plt.title('Correlation Matrix', fontsize=16)
plt.show()

# Covariance matrix
covariance_matrix = df[quantitative_vars].cov()

# Plotting the covariance matrix
plt.figure(figsize=(10, 8))
sns.heatmap(covariance_matrix, annot=True, fmt=".2f", cmap='coolwarm')
plt.title('Covariance Matrix', fontsize=16)
plt.show()

# Function to calculate the matrix of p-values for correlations
def calculate_pvalues(df):
    df = df.dropna()._get_numeric_data()
    dfcols = pd.DataFrame(columns=df.columns)
    pvalues = dfcols.transpose().join(dfcols, how='outer')
    for r in df.columns:
        for c in df.columns:
            pvalues[r][c] = round(pearsonr(df[r], df[c])[1], 4)
    return pvalues

# Calculating the matrix of p-values
pvalues_matrix = calculate_pvalues(df[quantitative_vars])

# Plotting the matrix of p-values
plt.figure(figsize=(10, 8))
sns.heatmap(pvalues_matrix.astype(float), annot=True, fmt=".4f", cmap='coolwarm', vmin=0, vmax=1)
plt.title('Matrix of P-values for Correlations', fontsize=16)
plt.show()

# Save results
pvalues_matrix.to_csv('06pvalues_matrix.csv', index=False)
correlation_matrix.to_csv('07correlation_matrix.csv', index=False)
covariance_matrix.to_csv('08covariance_matrix.csv', index=False)

## 14. Principal Component Analysis (PCA)

In [ ]:
# Redefining pca_normalized
pca_normalized = PCA(n_components=len(quantitative_vars))

# Redoing PCA using the min-max normalized data
principal_components_normalized = pca_normalized.fit_transform(df_min_max[quantitative_vars])
df_pca_normalized = pd.DataFrame(data=principal_components_normalized, columns=[f'PC{i+1}' for i in range(pca_normalized.n_components_)])

# Compute loading scores
loading_scores = pca_normalized.components_.T * np.sqrt(pca_normalized.explained_variance_)

# Plotting
plt.figure(figsize=(8, 6))

# Score plot
sns.scatterplot(x='PC1', y='PC2', data=df_pca_normalized, palette='viridis', label='Scores')
plt.title('PCA (Normalized Data): Score Plot (PC1 vs PC2)', fontsize=16)
plt.xlabel('Principal Component 1', fontsize=12)
plt.ylabel('Principal Component 2', fontsize=12)
plt.grid(True)

# Loading plot
for i, (x, y) in enumerate(zip(pca_normalized.components_[0], pca_normalized.components_[1])):
    plt.arrow(0, 0, x, y, color='r', alpha=0.5, width=0.005)
    plt.text(x, y, quantitative_vars[i], color='g', fontsize=12)

plt.show()

# 3D Graph
fig = plt.figure(figsize=(10, 8))
ax = fig.add_subplot(111, projection='3d')

# Score plot in 3D
ax.scatter(df_pca_normalized['PC1'], df_pca_normalized['PC2'], df_pca_normalized['PC3'], c='skyblue', s=60, label='Scores')
ax.view_init(30, 185)
ax.set_xlabel('Principal Component 1', fontsize=12)
ax.set_ylabel('Principal Component 2', fontsize=12)
ax.set_zlabel('Principal Component 3', fontsize=12)
plt.title('PCA (Normalized Data): 3D Score Plot (PC1 vs PC2 vs PC3)', fontsize=16)

# Loading plot in 3D
for i, (x, y, z) in enumerate(zip(loading_scores[:,0], loading_scores[:,1], loading_scores[:,2])):
    ax.text(x, y, z, quantitative_vars[i], color='g', fontsize=12)

plt.show()

# Variability Percentage
variance_percentage = pca_normalized.explained_variance_ratio_
for i, var in enumerate(variance_percentage):
    print(f"Variability of PC{i+1}: {var * 100:.2f}%")

# Calculate number of components to capture a certain percentage of variance
target_variance = 1.0  # Capture 100% of variance
cumulative_variance = np.cumsum(variance_percentage)
n_components_needed = np.argmax(cumulative_variance >= target_variance) + 1
print(f"Number of components capturing {target_variance * 100}% of variance: {n_components_needed}")

# Save PCA results to CSV
pca_results_df = pd.concat([df_pca_normalized, pd.DataFrame(data=loading_scores, columns=[f'Loading_PC{i+1}' for i in range(pca_normalized.n_components_)]),
                            pd.DataFrame(data=variance_percentage, columns=['Variability_Percentage'])], axis=1)
pca_results_df.to_csv('09pca_results.csv', index=False)

## 15. Hierarchical Clustering

In [ ]:
# Hierarchical clustering using the min-max normalized data
linkage_matrix_normalized = sch.linkage(df_min_max[quantitative_vars], method='ward')

# Plotting the hierarchical clustering as a dendrogram (Normalized Data)
plt.figure(figsize=(10, 7))
dendrogram = sch.dendrogram(linkage_matrix_normalized)
plt.title('Hierarchical Clustering (Normalized Data): Dendrogram', fontsize=16)
plt.xlabel('Samples', fontsize=12)
plt.ylabel('Euclidean distances', fontsize=12)
plt.show()

# Creating a cluster map (heatmap with dendrograms) for the min-max normalized data
sns.clustermap(df_min_max[quantitative_vars], cmap='coolwarm', figsize=(12, 12), method='ward', annot=True, fmt=".2f")
plt.title('Cluster Map with Dendrograms (Normalized Data)', fontsize=16, pad=100)
plt.show()

## 16. Data Normalization

In [ ]:
# Detect quantitative and categorical columns
quantitative_columns = df.select_dtypes(include=['int', 'float']).columns
categorical_columns = df.select_dtypes(include=['object', 'category']).columns

# Select quantitative data for normalization
Xmr = df[quantitative_columns]
print("Selected quantitative columns:", Xmr.columns.values.tolist())

# Min-max normalization
Xmr_min = Xmr.min()
Xmr_max = Xmr.max()
Xmnr = (Xmr - Xmr_min) / (Xmr_max - Xmr_min)

# Select categorical data
Xc = df[categorical_columns]
print("Selected categorical columns:", Xc.columns.values.tolist())

# Combine normalized quantitative data with categorical data
Xl = pd.concat([Xc, Xmnr], axis=1)

# Show column names of the resulting DataFrame
print("Columns after combining:", Xl.columns.values.tolist())

## 17. K-means Clustering and Heatmap

In [ ]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
from sklearn.preprocessing import StandardScaler
from scipy.cluster.hierarchy import linkage
from sklearn.cluster import KMeans

# Assuming Xl is your DataFrame
DT = Xl.copy()

# Set index
DT_index = DT.index

# Identify the first categorical column
categorical_columns = DT.select_dtypes(include=['object', 'category']).columns
if len(categorical_columns) > 0:
    group_column = categorical_columns[0]
else:
    raise ValueError("No categorical column found in the DataFrame.")

# Convert the group column to string to avoid mapping issues with categorical types
DT[group_column] = DT[group_column].astype(str)

# Standardize the data
scaler = StandardScaler()
quant_vars = DT.select_dtypes(include=['float64', 'int64']).columns
DT_scaled = scaler.fit_transform(DT[quant_vars])

# Perform hierarchical clustering
row_clusters = linkage(DT_scaled, method='ward')
col_clusters = linkage(DT_scaled.T, method='ward')

# Create a clustered DataFrame
clustered_df = pd.DataFrame(data=DT_scaled, columns=quant_vars, index=DT_index)
clustered_df['Group'] = DT[group_column]  # Add the group information

# Map groups to colors
group_colors = {group: color for group, color in zip(DT[group_column].unique(), sns.color_palette("hls", DT[group_column].nunique()))}
row_colors = DT[group_column].map(group_colors)  # Apply color mapping

# Create heatmap (Blue scale)
g1 = sns.clustermap(clustered_df.drop('Group', axis=1), row_linkage=row_clusters, col_linkage=col_clusters,
                    row_colors=row_colors, figsize=(12, 10), cmap='Blues', annot=False,
                    row_cluster=True, col_cluster=True)
plt.setp(g1.ax_heatmap.yaxis.get_majorticklabels(), rotation=0)  # Rotate y-axis labels
plt.savefig('heatmap_blue.png')

# Create heatmap (Grey scale)
g2 = sns.clustermap(clustered_df.drop('Group', axis=1), row_linkage=row_clusters, col_linkage=col_clusters,
                    row_colors=row_colors, figsize=(12, 10), cmap='Greys', annot=False,
                    row_cluster=True, col_cluster=True)
plt.setp(g2.ax_heatmap.yaxis.get_majorticklabels(), rotation=0)  # Rotate y-axis labels
plt.savefig('heatmap_grey.png')

# Get the order of rows and columns for Blue scale heatmap
ordered_cols = clustered_df.drop('Group', axis=1).columns[g1.dendrogram_col.reordered_ind]  # Use reordered indices
ordered_rows = clustered_df.index[g1.dendrogram_row.reordered_ind]  # Use reordered indices

# Create a DataFrame with ordered samples and their cluster group for Blue scale heatmap
ordered_sample_cluster_blue = pd.DataFrame({'Sample': ordered_rows, 'Cluster_Group': 'Sample'})
# Save to CSV
ordered_sample_cluster_blue.to_csv('sample_order_blue.csv', index=False)

# Create a DataFrame with ordered variables and their cluster group for Blue scale heatmap
ordered_variable_cluster_blue = pd.DataFrame({'Variable': ordered_cols, 'Cluster_Group': 'Variable'})
# Save to CSV
ordered_variable_cluster_blue.to_csv('variable_order_blue.csv', index=False)

# Get the order of rows and columns for Grey scale heatmap
ordered_cols_grey = clustered_df.drop('Group', axis=1).columns[g2.dendrogram_col.reordered_ind]  # Use reordered indices
ordered_rows_grey = clustered_df.index[g2.dendrogram_row.reordered_ind]  # Use reordered indices

# Create a DataFrame with ordered samples and their cluster group for Grey scale heatmap
ordered_sample_cluster_grey = pd.DataFrame({'Sample': ordered_rows_grey, 'Cluster_Group': 'Sample'})
# Save to CSV
ordered_sample_cluster_grey.to_csv('sample_order_grey.csv', index=False)

# Create a DataFrame with ordered variables and their cluster group for Grey scale heatmap
ordered_variable_cluster_grey = pd.DataFrame({'Variable': ordered_cols_grey, 'Cluster_Group': 'Variable'})
# Save to CSV
ordered_variable_cluster_grey.to_csv('variable_order_grey.csv', index=False)

# Add sample labels to the Blue scale heatmap
for label in ordered_rows:
    g1.ax_heatmap.annotate(label, xy=(0, ordered_rows.get_loc(label)), xytext=(-g1.ax_heatmap.yaxis.get_tick_padding(),
                                                                                0),
                           textcoords='offset points', va='center', ha='right', fontsize=8)

# Apply K-means clustering
kmeans = KMeans(n_clusters=4, random_state=0).fit(DT_scaled)
DT['KMeans_Cluster'] = kmeans.labels_

# Get cluster centroids
centroids = pd.DataFrame(scaler.inverse_transform(kmeans.cluster_centers_), columns=quant_vars)

# Add cluster label to centroids
centroids['Cluster'] = centroids.index

# Save the results to CSV
DT.to_csv('kmeans_with_groups.csv', index=True)  # Index is True to keep the original index
centroids.to_csv('kmeans_centroids.csv', index=False)  # Index is False since it's not relevant for centroids

## 18. PLS-DA Analysis

In [ ]:
import numpy as np
import pandas as pd
from sklearn.cross_decomposition import PLSRegression
from sklearn.model_selection import StratifiedShuffleSplit
from sklearn.metrics import accuracy_score
from sklearn.preprocessing import StandardScaler

# Define the PLS-DA model and cross-validation function
def perform_pls_cv(X, y, n_components, cv):
    accuracies = []
    for train_index, test_index in cv.split(X, y):
        X_train, X_test = X[train_index], X[test_index]
        y_train, y_test = y[train_index], y[test_index]

        pls = PLSRegression(n_components=n_components)
        pls.fit(X_train, y_train)
        y_pred = pls.predict(X_test)
        accuracies.append(accuracy_score(y_test, np.round(y_pred)))
    
    return np.mean(accuracies)

# Detect quantitative and categorical columns
quantitative_columns = Xl.select_dtypes(include=['int64', 'float64']).columns
categorical_columns = Xl.select_dtypes(include=['object', 'category']).columns

# Use the first categorical column as the target, if it exists
if len(categorical_columns) > 0:
    target_column = categorical_columns[0]
else:
    raise ValueError("No categorical columns found in the DataFrame for PLS-DA.")

# Separate features and target
X = Xl[quantitative_columns]
y = pd.Categorical(Xl[target_column]).codes

# Standardize features
scaler = StandardScaler()
X_scaled = scaler.fit_transform(X)

# Define cross-validation strategy
cv = StratifiedShuffleSplit(n_splits=10, test_size=0.33, random_state=42)

# Initialize an empty list to store DataFrame fragments
results_list = []

# Finding the optimal number of components
max_components = min(X_scaled.shape[1], 15)
optimal_components = 2
max_accuracy = 0

for n_components in range(2, max_components + 1):
    accuracy = perform_pls_cv(X_scaled, y, n_components, cv)
    results_list.append(pd.DataFrame({'Number_of_Components': [n_components], 'Average_Accuracy': [accuracy]}))

# Concatenate all DataFrame fragments into a single DataFrame
results_df = pd.concat(results_list, ignore_index=True)

# Save the results to a CSV file
results_df.to_csv('plsda_components_accuracy.csv', index=False)

# Find the optimal number of components
optimal_row = results_df.loc[results_df['Average_Accuracy'].idxmax()]
optimal_components = optimal_row['Number_of_Components']

# Print the optimal number of components
print(f"Optimal number of components: {optimal_components}")

## 19. PLS-DA Two-Class Analysis

In [ ]:
def calculate_vip(model, X):
    """
    Calculate Variable Importance in Projection (VIP) scores for a fitted PLS model.
    Args:
        model: Fitted PLSRegression model
        X: Original feature matrix used in training
    Returns:
        VIP scores for each feature
    """
    t = model.x_scores_  # Scores (T)
    w = model.x_weights_  # Weights (W)
    q = model.y_loadings_  # Loadings (Q)

    # Sum of squares of the scores (T^2) per component
    p = np.sum(t ** 2, axis=0) * q.flatten() ** 2  # Weighted by loadings
    w_squared = w ** 2  # Squared weights (features x components)

    # Correct the broadcasting
    vip_scores = np.sqrt(X.shape[1] * np.dot(w_squared, p) / np.sum(p))
    return vip_scores

# Standardize features
scaler = StandardScaler()
X_scaled = scaler.fit_transform(X)

# Define cross-validation strategy
cv = StratifiedShuffleSplit(n_splits=10, test_size=0.33, random_state=42)

# Define PLS-DA model
pls_da = PLSRegression(n_components=2)

# Initialize lists to store metrics and VIP scores
results = []
vip_scores_list = []

# Perform cross-validation
for fold_idx, (train_index, test_index) in enumerate(cv.split(X_scaled, y)):
    X_train, X_test = X_scaled[train_index], X_scaled[test_index]
    y_train, y_test = y[train_index], y[test_index]

    # Train PLS-DA model
    pls_da.fit(X_train, y_train)

    # Predict for training and testing sets
    y_train_pred = np.clip(np.round(pls_da.predict(X_train)), 0, 1).astype(int).flatten()
    y_test_pred = np.clip(np.round(pls_da.predict(X_test)), 0, 1).ast(int).flatten()

    # Training metrics
    train_cm = confusion_matrix(y_train, y_train_pred)
    train_tn, train_fp, train_fn, train_tp = train_cm.ravel()
    train_accuracy = accuracy_score(y_train, y_train_pred)
    train_sensitivity = train_tp / (train_tp + train_fn) if (train_tp + train_fn) > 0 else 0
    train_specificity = train_tn / (train_tn + train_fp) if (train_tn + train_fp) > 0 else 0

    # Testing metrics
    test_cm = confusion_matrix(y_test, y_test_pred)
    test_tn, test_fp, test_fn, test_tp = test_cm.ravel()
    test_accuracy = accuracy_score(y_test, y_test_pred)
    test_sensitivity = test_tp / (test_tp + test_fn) if (test_tp + test_fn) > 0 else 0
    test_specificity = test_tn / (test_tn + test_fp) if (test_tn + test_fp) > 0 else 0

    # Calculate VIP scores for the current fold
    vip_scores = calculate_vip(pls_da, X_train)
    vip_scores_list.append(vip_scores)

    # Append results
    results.append({
        'Fold': fold_idx + 1,
        'Train Accuracy': train_accuracy,
        'Train Sensitivity': train_sensitivity,
        'Train Specificity': train_specificity,
        'Train Confusion Matrix': train_cm.tolist(),
        'Test Accuracy': test_accuracy,
        'Test Sensitivity': test_sensitivity,
        'Test Specificity': test_specificity,
        'Test Confusion Matrix': test_cm.tolist()
    })

# Average VIP scores across folds
average_vip_scores = np.mean(vip_scores_list, axis=0)

# Combine results into a DataFrame
results_df = pd.DataFrame(results)

# Add VIP scores to the DataFrame
for i, feature in enumerate(X.columns):
    results_df[f'VIP_{feature}'] = average_vip_scores[i]

# Save results to a CSV file
results_df.to_csv('plsda_train_test_metrics_with_vip.csv', index=False)

# Display results
print(results_df)

## End of Analysis